# Optunaの動作確認サンプル

ハイパーパラメータの自動チューニングができるライブラリ[Optuna](https://www.preferred.jp/ja/projects/optuna/)の動作確認を行う．  
機械学習モデルの開発において，精度向上の最後の一押しを効率化できる．

[GBDTの試行](https://qiita.com/DS27/items/aa3f6d0f03a8053e5810#6-gbdt%E5%8B%BE%E9%85%8D%E3%83%96%E3%83%BC%E3%82%B9%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%E6%9C%A8%E3%81%AB%E3%81%A4%E3%81%84%E3%81%A6)で高い精度が得られており，このモデルをハイパーパラメータチューニングのベースラインとする．

## データセットの読み込み(ボストン住宅価格)

In [1]:
from sklearn.datasets import load_boston
import pandas as pd

boston = load_boston()
df_x_boston = pd.DataFrame(boston['data'], columns=boston['feature_names'])
df_y_boston = pd.DataFrame(boston['target'], columns=['MEDV'])
df_boston = pd.concat([df_x_boston, df_y_boston], axis=1)

### 欠損値確認

In [2]:
df_boston.isnull().sum()

CRIM       0
ZN         0
INDUS      0
CHAS       0
NOX        0
RM         0
AGE        0
DIS        0
RAD        0
TAX        0
PTRATIO    0
B          0
LSTAT      0
MEDV       0
dtype: int64

### 学習データと評価データの分割

In [3]:
from sklearn.model_selection import train_test_split

x_train, x_test, y_train, y_test = train_test_split(df_x_boston, df_y_boston, test_size=0.3, random_state=0)

### データの標準化

In [4]:
from sklearn.preprocessing import StandardScaler
sc = StandardScaler()
sc.fit(x_train)
x_train_std = sc.transform(x_train)
x_test_std = sc.transform(x_test)

## GBDTの学習と評価

In [5]:
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.metrics import r2_score
from sklearn.metrics import mean_squared_error

gbr = GradientBoostingRegressor()
gbr.fit(x_train_std, y_train)

pred_gbr = gbr.predict(x_test_std)
r2_gbr = r2_score(y_test, pred_gbr)
mse_gbr = mean_squared_error(y_test, pred_gbr)

print("R2 : %.3f" % r2_gbr)
print("MSE : %.3f" % mse_gbr)

R2 : 0.846
MSE : 12.821


/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


### Optuna

GradientBoostingRegressorデフォルト値

```
class sklearn.ensemble.GradientBoostingRegressor(*, loss='squared_error', learning_rate=0.1, n_estimators=100, subsample=1.0, criterion='friedman_mse', min_samples_split=2, min_samples_leaf=1, min_weight_fraction_leaf=0.0, max_depth=3, min_impurity_decrease=0.0, init=None, random_state=None, max_features=None, alpha=0.9, verbose=0, max_leaf_nodes=None, warm_start=False, validation_fraction=0.1, n_iter_no_change=None, tol=0.0001, ccp_alpha=0.0)
```


In [6]:
import optuna

In [7]:
def objective(trial):
    lr = trial.suggest_loguniform('learning_rate', 0.001, 0.1)
    n_estimators = trial.suggest_int('n_estimators', 10, 1000)
    min_samples_split = trial.suggest_int('min_samples_split', 2, 10)
    min_samples_leaf = trial.suggest_int('min_samples_leaf', 1, 10)
    max_depth = trial.suggest_int('max_depth', 1, 10)
    
    gbr = GradientBoostingRegressor(
        learning_rate=lr, 
        n_estimators=n_estimators, 
        min_samples_split=min_samples_split,
        min_samples_leaf=min_samples_leaf,
        max_depth=max_depth)
    gbr.fit(x_train_std, y_train)
    
    pred_gbr = gbr.predict(x_test_std)
    r2_gbr = r2_score(y_test, pred_gbr)

    return 1-r2_gbr

n_trials = 10000
study = optuna.create_study()
study.optimize(objective, n_trials=n_trials)

[I 2022-06-12 05:12:36,181] A new study created in memory with name: no-name-04eefd5e-b2c0-47e1-9d7f-ffdc84ffee03
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 05:12:36,453] Trial 0 finished with value: 0.3040799560436682 and parameters: {'learning_rate': 0.0035488694296649317, 'n_estimators': 355, 'min_samples_split': 2, 'min_samples_leaf': 5, 'max_depth': 4}. Best is trial 0 with value: 0.3040799560436682.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 05:12:37,035] Trial 1 finished with value: 0.16118228519749622 and parameters: {'learning_rate':

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 05:12:43,637] Trial 16 finished with value: 0.17088955686825824 and parameters: {'learning_rate': 0.02299572230887197, 'n_estimators': 954, 'min_samples_split': 10, 'min_samples_leaf': 2, 'max_depth': 5}. Best is trial 1 with value: 0.16118228519749622.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 05:12:44,013] Trial 17 finished with value: 0.2581057247852696 and parameters: {'learning_rate': 0.00529665363074133, 'n_estimators': 799, 'min_samples_split': 8, 'min_samples_leaf': 6, 'max_depth': 2}. Best 

[I 2022-06-12 05:12:53,362] Trial 31 finished with value: 0.15780195579941558 and parameters: {'learning_rate': 0.01410943872504453, 'n_estimators': 997, 'min_samples_split': 3, 'min_samples_leaf': 2, 'max_depth': 4}. Best is trial 26 with value: 0.14719375426970915.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 05:12:53,956] Trial 32 finished with value: 0.17341634586112664 and parameters: {'learning_rate': 0.014996873155297621, 'n_estimators': 982, 'min_samples_split': 2, 'min_samples_leaf': 2, 'max_depth': 3}. Best is trial 26 with value: 0.14719375426970915.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for exam

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 05:13:04,950] Trial 47 finished with value: 0.15828612296324907 and parameters: {'learning_rate': 0.05312566769586736, 'n_estimators': 638, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 6}. Best is trial 26 with value: 0.14719375426970915.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 05:13:05,753] Trial 48 finished with value: 0.1606132989443545 and parameters: {'learning_rate': 0.047192322093798145, 'n_estimators': 647, 'min_samples_split': 5, 'min_samples_leaf': 1, 'max_depth': 8}. Best

[I 2022-06-12 05:13:14,139] Trial 62 finished with value: 0.1641070432658528 and parameters: {'learning_rate': 0.08025512593946851, 'n_estimators': 415, 'min_samples_split': 3, 'min_samples_leaf': 1, 'max_depth': 7}. Best is trial 51 with value: 0.14573008264058784.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 05:13:14,860] Trial 63 finished with value: 0.16607131115808704 and parameters: {'learning_rate': 0.03978963215757982, 'n_estimators': 563, 'min_samples_split': 2, 'min_samples_leaf': 1, 'max_depth': 8}. Best is trial 51 with value: 0.14573008264058784.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for exampl

...

[I 2022-06-12 07:23:21,663] Trial 9922 finished with value: 0.14733703973733037 and parameters: {'learning_rate': 0.04018343412525881, 'n_estimators': 556, 'min_samples_split': 7, 'min_samples_leaf': 1, 'max_depth': 7}. Best is trial 6184 with value: 0.13556959049580586.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 07:23:22,721] Trial 9923 finished with value: 0.16790956161716675 and parameters: {'learning_rate': 0.031404874821908596, 'n_estimators': 576, 'min_samples_split': 7, 'min_samples_leaf': 2, 'max_depth': 7}. Best is trial 6184 with value: 0.13556959049580586.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), 

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 07:23:38,818] Trial 9938 finished with value: 0.14834145912328955 and parameters: {'learning_rate': 0.04537842097629277, 'n_estimators': 576, 'min_samples_split': 7, 'min_samples_leaf': 1, 'max_depth': 7}. Best is trial 6184 with value: 0.13556959049580586.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 07:23:39,841] Trial 9939 finished with value: 0.15348657456938009 and parameters: {'learning_rate': 0.03817465870456375, 'n_estimators': 553, 'min_samples_split': 6, 'min_samples_leaf': 1, 'max_depth': 7}

[I 2022-06-12 07:23:53,835] Trial 9953 finished with value: 0.20052838132397066 and parameters: {'learning_rate': 0.04408038361593915, 'n_estimators': 559, 'min_samples_split': 6, 'min_samples_leaf': 6, 'max_depth': 7}. Best is trial 6184 with value: 0.13556959049580586.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 07:23:54,692] Trial 9954 finished with value: 0.15844629327628856 and parameters: {'learning_rate': 0.022828939850464438, 'n_estimators': 285, 'min_samples_split': 7, 'min_samples_leaf': 1, 'max_depth': 8}. Best is trial 6184 with value: 0.13556959049580586.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), 

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 07:24:09,625] Trial 9969 finished with value: 0.15293000837484594 and parameters: {'learning_rate': 0.03226034050988778, 'n_estimators': 520, 'min_samples_split': 6, 'min_samples_leaf': 1, 'max_depth': 7}. Best is trial 6184 with value: 0.13556959049580586.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 07:24:10,667] Trial 9970 finished with value: 0.141987944786238 and parameters: {'learning_rate': 0.04225747394389053, 'n_estimators': 560, 'min_samples_split': 7, 'min_samples_leaf': 1, 'max_depth': 7}. 

[I 2022-06-12 07:24:25,003] Trial 9984 finished with value: 0.1422311942820893 and parameters: {'learning_rate': 0.028170167798482366, 'n_estimators': 531, 'min_samples_split': 7, 'min_samples_leaf': 1, 'max_depth': 7}. Best is trial 6184 with value: 0.13556959049580586.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)
[I 2022-06-12 07:24:26,022] Trial 9985 finished with value: 0.15467629494757995 and parameters: {'learning_rate': 0.03297550342288497, 'n_estimators': 451, 'min_samples_split': 8, 'min_samples_leaf': 1, 'max_depth': 7}. Best is trial 6184 with value: 0.13556959049580586.
/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), f

In [8]:
study.best_trial

FrozenTrial(number=6184, values=[0.13556959049580586], datetime_start=datetime.datetime(2022, 6, 12, 6, 25, 27, 269671), datetime_complete=datetime.datetime(2022, 6, 12, 6, 25, 28, 288115), params={'learning_rate': 0.03867081978009032, 'n_estimators': 635, 'min_samples_split': 7, 'min_samples_leaf': 1, 'max_depth': 7}, distributions={'learning_rate': LogUniformDistribution(high=0.1, low=0.001), 'n_estimators': IntUniformDistribution(high=1000, low=10, step=1), 'min_samples_split': IntUniformDistribution(high=10, low=2, step=1), 'min_samples_leaf': IntUniformDistribution(high=10, low=1, step=1), 'max_depth': IntUniformDistribution(high=10, low=1, step=1)}, user_attrs={}, system_attrs={}, intermediate_values={}, trial_id=6184, state=TrialState.COMPLETE, value=None)

In [9]:
study.best_trial.params

{'learning_rate': 0.03867081978009032,
 'n_estimators': 635,
 'min_samples_split': 7,
 'min_samples_leaf': 1,
 'max_depth': 7}

In [10]:
params = study.best_trial.params
lr = params['learning_rate']
n_estimators = params['n_estimators']
min_samples_split = params['min_samples_split']
min_samples_leaf = params['min_samples_leaf']
max_depth = params['max_depth']

gbr = GradientBoostingRegressor(
    learning_rate=lr, 
    n_estimators=n_estimators, 
    min_samples_split=min_samples_split,
    min_samples_leaf=min_samples_leaf,
    max_depth=max_depth)
gbr.fit(x_train_std, y_train)

pred_gbr = gbr.predict(x_test_std)
r2_gbr = r2_score(y_test, pred_gbr)
mse_gbr = mean_squared_error(y_test, pred_gbr)

print("R2 : %.3f" % r2_gbr)
print("MSE : %.3f" % mse_gbr)

/usr/local/lib/python3.8/dist-packages/sklearn/utils/validation.py:63: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  return f(*args, **kwargs)


R2 : 0.864
MSE : 11.358
